# Voting, Stacking and Blending

In [1]:
%pylab inline
import numpy as np
import pandas as pd
import pylab as plt

import warnings
warnings.filterwarnings("ignore")

Populating the interactive namespace from numpy and matplotlib


/anaconda3/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


# Задача регрессии

In [2]:
from sklearn.datasets import load_boston

data = load_boston()

X_full = data.data
y_full = data.target

In [3]:
from sklearn.model_selection import train_test_split
X, X_test, y, y_test = train_test_split(X_full, y_full, test_size=100, 
                                        random_state=241)
Xtrain, Xval, ytrain, yval = train_test_split(X, y, test_size=0.35, 
                                        random_state=241)

In [4]:
from sklearn.model_selection import KFold, cross_val_score
cv = KFold(Xtrain.shape[0], shuffle=True, random_state=241)

In [5]:
from sklearn.ensemble import RandomForestRegressor
rf = RandomForestRegressor()
print(cross_val_score(rf, Xtrain, ytrain, cv=cv, scoring ='neg_mean_squared_error').mean())

/anaconda3/lib/python3.6/site-packages/sklearn/ensemble/weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d


-14.552877566539923


In [6]:
from sklearn.metrics import mean_squared_error

rf.fit(Xtrain, ytrain)
pred_rf = rf.predict(Xval)
mean_squared_error(pred_rf, yval)

10.765420979020977

In [7]:
from sklearn.ensemble import AdaBoostRegressor
ada = AdaBoostRegressor()
print(cross_val_score(ada, Xtrain, ytrain, cv=cv, scoring ='neg_mean_squared_error').mean())

-15.070248035915098


In [8]:
ada.fit(Xtrain, ytrain)
pred_ada = ada.predict(Xval)
mean_squared_error(pred_ada, yval)

13.104286188421193

# Blending

1) смешаем алгоритмы с весами 1:1, то есть в качестве ответа предскажем среднее значение смеси

In [38]:
pred_rf.shape

(143,)

In [39]:
pred_ada.shape

(143,)

In [9]:
pred_mix_1 = 0.5 *(pred_rf + pred_ada)
print('Validation prediction:',mean_squared_error(pred_mix_1, yval))

rf_test = rf.predict(X_test)
ada_test = ada.predict(X_test)
pred_test_1 = 0.5 *(rf_test + ada_test)
print('Test prediction:',mean_squared_error(pred_test_1, y_test))

Validation prediction: 10.378655211236817
Test prediction: 11.10678204626636


2) Смешаем алгоритмы с весами $\alpha$ : $1-\alpha$. Подберём $\alpha$ в цикле

In [10]:
max_score = -100
opt_alpha = 0

for alpha in np.arange(0.01,1.01,0.01):
    pred_mix_2 = alpha * pred_rf + (1-alpha) * pred_ada
    curr_score = -mean_squared_error(pred_mix_2, yval)
    
    if curr_score > max_score:
        max_score = curr_score
        opt_alpha = alpha
        
print(opt_alpha, -max_score)

0.6900000000000001 10.158985866437503


In [11]:
rf_test = rf.predict(X_test)
ada_test = ada.predict(X_test)
pred_test_2 = opt_alpha * rf_test + (1-opt_alpha) * ada_test
print('Test prediction:',mean_squared_error(pred_test_2, y_test))

Test prediction: 12.362884174049999


# Stacking

In [12]:
SecondTrain = pd.DataFrame(np.nan, index=np.arange(len(Xval)), columns=['RF','ADA'])

SecondTrain['RF'] = rf.predict(Xval)
SecondTrain['ADA'] = ada.predict(Xval)

In [13]:
meta = RandomForestRegressor()
meta.fit(SecondTrain,yval)

RandomForestRegressor(bootstrap=True, criterion='mse', max_depth=None,
           max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=10, n_jobs=1,
           oob_score=False, random_state=None, verbose=0, warm_start=False)

In [14]:
rf_test = rf.predict(X_test)
ada_test = ada.predict(X_test)

FirstLevelPred = pd.DataFrame(np.nan, index=np.arange(len(X_test)), columns=['RF','ADA'])

FirstLevelPred['RF'] = rf.predict(X_test)
FirstLevelPred['ADA'] = ada.predict(X_test)

In [15]:
final_pred = meta.predict(FirstLevelPred)

print('Final prediction:',mean_squared_error(final_pred,y_test))

Final prediction: 10.659046777777776


# Задача классификации

In [16]:
from sklearn.datasets import load_iris

data = load_iris()

X_full = data.data
y_full = data.target

In [17]:
X, X_test, y, y_test = train_test_split(X_full, y_full, test_size=100, 
                                        random_state=135)

In [18]:
from sklearn.model_selection import KFold, cross_val_score
cv = KFold(X.shape[0], shuffle=True, random_state=123)

In [19]:
from sklearn.ensemble import RandomForestClassifier
rf = RandomForestClassifier()
print(cross_val_score(rf, X, y, cv=cv, scoring ='accuracy').mean())

0.9


In [20]:
from sklearn.linear_model import LogisticRegression
lr = LogisticRegression()
print(cross_val_score(lr, X, y, cv=cv, scoring ='accuracy').mean())

0.88


# Voting

In [21]:
from sklearn.ensemble import VotingClassifier
from sklearn.metrics import accuracy_score

voting = VotingClassifier(estimators=[('RF',rf),('LR',lr)], voting='soft')
voting.fit(X, y)
pred_voting = voting.predict(X_test)

print('Accuracy on test:', accuracy_score(pred_voting,y_test))

Accuracy on test: 0.95


/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:


# Задание

1) Разбейте X, y на тренировочную и валидационную части

2) Сделайте предсказание с помощью блендинга (предсказывайте вероятности классов, а не сами классы - методом predict_proba)

3) Сделайте предсказание с помощью стекинга (предсказывайте вероятности классов)

**Blending**

In [31]:
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
rf = RandomForestClassifier()
ada = AdaBoostClassifier()
lr = LogisticRegression()

In [81]:
#Your code here
X, X_test, y, y_test = train_test_split(X_full, y_full, test_size=0.2, random_state=135)
Xtrain, Xval, ytrain, yval = train_test_split(X, y, test_size=0.30, 
                                        random_state=135)
rf.fit(X, y)
ada.fit(X, y)
lr.fit(X, y)

pred_proba_rf = rf.predict_proba(Xval)
pred_proba_lr = lr.predict_proba(Xval)
pred_proba_ada = ada.predict_proba(Xval)

In [87]:
pred_mix_1 = 0.5 *(pred_proba_lr + pred_proba_ada)

In [90]:
pred_mix_1 = [list(i).index(max(i)) for i in pred_mix_1]

In [91]:
print('Validation prediction:', mean_squared_error(pred_mix_1, yval))

lr_test = lr.predict(X_test)
ada_test = ada.predict(X_test)
pred_test_1 = 0.5 *(lr_test + ada_test)
print('Test prediction:', mean_squared_error(pred_test_1, y_test))

Validation prediction: 0.027777777777777776
Test prediction: 0.0


In [92]:
max_score = -100
opt_alpha = 0

for alpha in np.arange(0.01,1.01,0.01):
    pred_mix_2 = alpha * pred_proba_lr + (1-alpha) * pred_proba_ada
    pred_mix_2 = [list(i).index(max(i)) for i in pred_mix_2]
    curr_score = -mean_squared_error(pred_mix_2, yval)
    
    if curr_score > max_score:
        max_score = curr_score
        opt_alpha = alpha
        
print(opt_alpha, -max_score)

0.08 0.027777777777777776


# **Stacking**

In [ ]:
#Your code here

# Готовое решение для stacking

Вернемся к задаче регрессии с датасетом Boston.

In [94]:
from vecstack import stacking

In [ ]:
models = [RandomForestRegressor(),AdaBoostRegressor()]

S_train, S_test = stacking(models, X, y, X_test, regression=True, verbose=1)

In [ ]:
meta = RandomForestRegressor()
meta.fit(S_train, y)

In [ ]:
final_pred = meta.predict(S_test)

print('Final prediction:',mean_squared_error(final_pred,y_test))

# Задание

Используйте библиотеку vecstack для решения задачи классификации Iris с помощью stacking

In [95]:
#your code here
from sklearn.datasets import load_iris
data = load_iris()
X_full = data.data
y_full = data.target
X, X_test, y, y_test = train_test_split(X_full, y_full, test_size=100, random_state=135)
models = [LogisticRegression(), RandomForestClassifier()]
S_train, S_test = stacking(models, X, y, X_test, regression=True, verbose=1)

task:         [regression]
metric:       [mean_absolute_error]
mode:         [oof_pred_bag]
n_models:     [2]

model  0:     [LogisticRegression]
    ----
    MEAN:     [0.14583333] + [0.17052818]
    FULL:     [0.14000000]

model  1:     [RandomForestClassifier]
    ----
    MEAN:     [0.06089744] + [0.03525641]
    FULL:     [0.06000000]



In [96]:
meta = LogisticRegression()
meta.fit(S_train, y)

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False)

In [97]:
final_pred = meta.predict(S_test)

print('Final prediction:',mean_squared_error(final_pred,y_test))

Final prediction: 0.19


# Задание

Решите задачу с данными train_medium.csv, test_medium.csv, используя stacking и/или blending нескольких алгоритмов. Сравните полученное качество (на кросс-валидации) с качеством, полученным с помощью xgboost, catboost, lightgbm в отдельности.

In [1]:
#your code here
import pandas as pd
train_data = pd.read_csv("train_medium.csv")
test_data = pd.read_csv("test_medium.csv") 

/anaconda3/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: numpy.dtype size changed, may indicate binary incompatibility. Expected 96, got 88
  return f(*args, **kwds)


In [2]:
train_data.head()

Unnamed: 0  Existing_EMI  Loan_Amount_Applied  Loan_Tenure_Applied  \
0        7881           0.0             100000.0                  3.0   
1         189       21000.0             450000.0                  5.0   
2       64000        3832.0             100000.0                  3.0   
3       61629           0.0             200000.0                  3.0   
4       23212           0.0              50000.0                  1.0   

   Monthly_Income  Var4  Var5  Age  EMI_Loan_Submitted_Missing  \
0           29000     4    11   29                           0   
1           48000     1     0   27                           1   
2           25000     5    11   44                           0   
3           22500     3     1   26                           1   
4           17943     1     0   25                           1   

   Interest_Rate_Missing    ...      Var2_3  Var2_4  Var2_5  Var2_6  \
0                      0    ...           0       0       0       0   
1                      1    ...           0       0       0       0   
2                      0    ...           0       0       0       1   
3                      1    ...           0       0       0       1   
4                      1    ...           0       0       0       0   

   Mobile_Verified_0  Mobile_Verified_1  Source_0  Source_1  Source_2  \
0                  0                  1         0         1         0   
1                  1                  0         0         1         0   
2                  0                  1         1         0         0   
3                  0                  1         1         0         0   
4                  1                  0         0         1         0   

   Disbursed  
0        1.0  
1        0.0  
2        0.0  
3        0.0  
4        0.0  

[5 rows x 51 columns]

In [3]:
test_data.head()

Unnamed: 0  Existing_EMI  Loan_Amount_Applied  Loan_Tenure_Applied  \
0       27487           0.0             300000.0                  5.0   
1       56689           0.0              50000.0                  1.0   
2       47624           0.0                  0.0                  0.0   
3       38700       11500.0             500000.0                  4.0   
4       12905        8000.0             200000.0                  4.0   

   Monthly_Income  Var4  Var5  Age  EMI_Loan_Submitted_Missing  \
0           22000     2     3   28                           1   
1           20000     3     1   34                           1   
2            5000     7     0   22                           1   
3          200000     5    10   41                           0   
4           20500     3     1   26                           1   

   Interest_Rate_Missing    ...      Var2_3  Var2_4  Var2_5  Var2_6  \
0                      1    ...           0       0       0       0   
1                      1    ...           0       0       0       1   
2                      1    ...           1       0       0       0   
3                      0    ...           0       0       0       0   
4                      1    ...           0       0       0       0   

   Mobile_Verified_0  Mobile_Verified_1  Source_0  Source_1  Source_2  \
0                  0                  1         0         0         1   
1                  0                  1         1         0         0   
2                  1                  0         1         0         0   
3                  0                  1         1         0         0   
4                  1                  0         0         1         0   

   Disbursed  
0        0.0  
1        0.0  
2        0.0  
3        0.0  
4        0.0  

[5 rows x 51 columns]

In [4]:
y_train = train_data['Disbursed']
y_test = test_data['Disbursed']

In [5]:
X_train = train_data.drop(columns=['Disbursed'])
X_test = test_data.drop(columns=['Disbursed'])

In [6]:
'Disbursed' in X_train.columns

False

In [7]:
'Disbursed' in X_test.columns

False

In [97]:
from vecstack import stacking
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import mean_squared_error

In [98]:
param_grid = {'penalty': ['l2'], 'solver': ['newton-cg', 'lbfgs', 'liblinear', 'sag', 'saga']}
lr = LogisticRegression()
clf = GridSearchCV(lr, param_grid, cv=12, scoring = 'mean_squared_error')
clf.fit(X_train, y_train)
clf.best_score_, clf.best_params_

/anaconda3/lib/python3.6/site-packages/scipy/optimize/linesearch.py:462: LineSearchWarning: The line search algorithm did not converge
  warn('The line search algorithm did not converge', LineSearchWarning)
/anaconda3/lib/python3.6/site-packages/scipy/optimize/linesearch.py:313: LineSearchWarning: The line search algorithm did not converge
  warn('The line search algorithm did not converge', LineSearchWarning)
/anaconda3/lib/python3.6/site-packages/sklearn/utils/optimize.py:203: ConvergenceWarning: newton-cg failed to converge. Increase the number of iterations.
  "number of iterations.", ConvergenceWarning)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mea

/anaconda3/lib/python3.6/site-packages/sklearn/utils/optimize.py:203: ConvergenceWarning: newton-cg failed to converge. Increase the number of iterations.
  "number of iterations.", ConvergenceWarning)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWar

/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/m

/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mea

/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mean_squared_error was renamed to neg_mean_squared_error in version 0.18 and will be removed in 0.20.
  sample_weight=sample_weight)
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/anaconda3/lib/python3.6/site-packages/sklearn/metrics/scorer.py:100: DeprecationWarning: Scoring method mea

(-0.014540718608748946, {'penalty': 'l2', 'solver': 'sag'})

In [96]:
rfc=RandomForestClassifier(random_state=42)
param_grid = { 
    'n_estimators': [200, 500],
    'max_features': ['auto', 'sqrt', 'log2'],
    'max_depth' : [4,5,6,7,8],
    'criterion' :['gini', 'entropy']
}
CV_rfc = GridSearchCV(estimator=rfc, param_grid=param_grid, cv= 5)
CV_rfc.fit(X_train, y_train)
CV_rfc.best_score_, CV_rfc.best_params_

(0.985459281391251,
 {'criterion': 'gini',
  'max_depth': 4,
  'max_features': 'auto',
  'n_estimators': 200})

In [101]:
models = [
        LogisticRegression(penalty='l2', solver='sag'), 
        RandomForestClassifier(criterion='gini',
                               max_depth=4,
                               max_features='auto',
                               n_estimators=200)
     ]
S_train, S_test = stacking(models, X_train, y_train, X_test, regression=True, verbose=1)

task:         [regression]
metric:       [mean_absolute_error]
mode:         [oof_pred_bag]
n_models:     [2]

model  0:     [LogisticRegression]


/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/sag.py:326: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  "the coef_ did not converge", ConvergenceWarning)


    ----
    MEAN:     [0.01454073] + [0.00054747]
    FULL:     [0.01454072]

model  1:     [RandomForestClassifier]
    ----
    MEAN:     [0.01454073] + [0.00054747]
    FULL:     [0.01454072]



In [102]:
meta = RandomForestRegressor()
meta.fit(S_train, y_train)

RandomForestRegressor(bootstrap=True, criterion='mse', max_depth=None,
           max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=10, n_jobs=1,
           oob_score=False, random_state=None, verbose=0, warm_start=False)

In [103]:
final_pred = meta.predict(S_test)
print('Final prediction:', mean_squared_error(final_pred, y_test))

Final prediction: 0.014671397976517413


Сравните полученное качество (на кросс-валидации) с качеством, полученным с помощью xgboost, catboost, lightgbm в отдельности.

XGboost

In [23]:
from sklearn.model_selection import GridSearchCV
import xgboost as xgb

In [25]:
alg = xgb.XGBClassifier(objective='binary:logistic')
clf = GridSearchCV(alg,{'max_depth': [2,4,6,8,10],
                    'n_estimators': [50,100,200,400]}, 
                    verbose=1, 
                    scoring='neg_log_loss')

clf.fit(X_train, y_train)
clf.best_score_, clf.best_params_

Fitting 3 folds for each of 20 candidates, totalling 60 fits


[Parallel(n_jobs=1)]: Done  60 out of  60 | elapsed: 21.8min finished


(-0.06428085204612362, {'max_depth': 4, 'n_estimators': 100})

In [35]:
alg = xgb.XGBClassifier(objective='binary:logistic', n_estimators=100, max_depth=4)
xgb_m = alg.fit(X_train, y_train)

In [40]:
xgb_pred = xgb_m.predict(X_test)
print('Final prediction:', mean_squared_error(xgb_pred, y_test))

Final prediction: 0.01489312801654792


/anaconda3/lib/python3.6/site-packages/sklearn/preprocessing/label.py:151: DeprecationWarning: The truth value of an empty array is ambiguous. Returning False, but in future this will result in an error. Use `array.size > 0` to check that an array is not empty.
  if diff:


CatBoost

In [62]:
for column in X_train.columns:
    vals = X_train[column].unique()
    print(column, vals, len(vals))

Unnamed: 0 [ 7881   189 64000 ... 65680 76523 78252] 65265
Existing_EMI [    0. 21000.  3832. ... 29544. 36386.  4206.] 3110
Loan_Amount_Applied [1.000000e+05 4.500000e+05 2.000000e+05 5.000000e+04 0.000000e+00
 5.000000e+05 3.000000e+05 2.300000e+05 1.000000e+06 6.500000e+04
 1.500000e+06 7.000000e+05 1.200000e+05 7.000000e+04 2.000000e+06
 6.000000e+05 1.500000e+04 2.500000e+06 8.000000e+05 2.500000e+05
 6.000000e+04 3.000000e+06 4.000000e+05 5.000000e+06 1.500000e+05
 1.450000e+05 4.000000e+04 3.500000e+05 2.500000e+04 6.000000e+00
 4.000000e+06 8.000000e+04 7.600000e+05 1.300000e+06 2.000000e+04
 7.500000e+05 3.000000e+04 5.500000e+04 9.500000e+04 8.000000e+00
 1.750000e+06 1.200000e+06 1.400000e+05 1.130000e+05 1.600000e+05
 2.100000e+06 2.800000e+05 2.500000e+01 7.500000e+04 5.600000e+04
 3.000000e+01 1.000000e+04 1.400000e+06 2.600000e+06 1.800000e+05
 6.700000e+04 4.300000e+05 3.600000e+05 1.300000e+05 1.850000e+05
 1.100000e+06 2.160000e+05 9.000000e+05 1.750000e+05 6.000000e+

In [85]:
cat_features = []
    
for column in list(X_train.columns):
    if len(X_train[column].unique()) < 60:
        cat_features.append(list(X_train.columns).index(column))

In [86]:
cat_features

[3,
 5,
 6,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49]

In [88]:
from catboost import Pool, CatBoostClassifier
params = {'depth': [4, 6, 8],
          'random_seed' : [400, 100, 200],
          'learning_rate' : [0.01, 0.03, 0.1]}
cb = CatBoostClassifier(loss_function='MultiClass', iterations = 500, learning_rate=0.03)
clf = GridSearchCV(cb, params, scoring='neg_mean_squared_error', cv = 5)
clf.fit(X_train, y_train, cat_features = cat_features)
clf.best_score_, clf.best_params_

0:	learn: -0.6837877	total: 54.8ms	remaining: 27.3s
1:	learn: -0.6746151	total: 102ms	remaining: 25.4s
2:	learn: -0.6656200	total: 148ms	remaining: 24.6s
3:	learn: -0.6567956	total: 194ms	remaining: 24s
4:	learn: -0.6481460	total: 245ms	remaining: 24.2s
5:	learn: -0.6396595	total: 304ms	remaining: 25.1s
6:	learn: -0.6313364	total: 364ms	remaining: 25.7s
7:	learn: -0.6231685	total: 409ms	remaining: 25.1s
8:	learn: -0.6151496	total: 455ms	remaining: 24.8s
9:	learn: -0.6072843	total: 501ms	remaining: 24.5s
10:	learn: -0.5995567	total: 558ms	remaining: 24.8s
11:	learn: -0.5919735	total: 608ms	remaining: 24.7s
12:	learn: -0.5845287	total: 652ms	remaining: 24.4s
13:	learn: -0.5772146	total: 696ms	remaining: 24.1s
14:	learn: -0.5700306	total: 746ms	remaining: 24.1s
15:	learn: -0.5629769	total: 809ms	remaining: 24.5s
16:	learn: -0.5560469	total: 862ms	remaining: 24.5s
17:	learn: -0.5492330	total: 921ms	remaining: 24.7s
18:	learn: -0.5425360	total: 971ms	remaining: 24.6s
19:	learn: -0.5359571	t

161:	learn: -0.1478843	total: 8.69s	remaining: 18.1s
162:	learn: -0.1469529	total: 8.74s	remaining: 18.1s
163:	learn: -0.1460317	total: 8.8s	remaining: 18s
164:	learn: -0.1451090	total: 8.85s	remaining: 18s
165:	learn: -0.1442063	total: 8.9s	remaining: 17.9s
166:	learn: -0.1433186	total: 8.96s	remaining: 17.9s
167:	learn: -0.1424464	total: 9.01s	remaining: 17.8s
168:	learn: -0.1415655	total: 9.05s	remaining: 17.7s
169:	learn: -0.1407104	total: 9.1s	remaining: 17.7s
170:	learn: -0.1398526	total: 9.17s	remaining: 17.6s
171:	learn: -0.1390016	total: 9.23s	remaining: 17.6s
172:	learn: -0.1381637	total: 9.28s	remaining: 17.5s
173:	learn: -0.1373335	total: 9.34s	remaining: 17.5s
174:	learn: -0.1365162	total: 9.42s	remaining: 17.5s
175:	learn: -0.1357196	total: 9.48s	remaining: 17.5s
176:	learn: -0.1349265	total: 9.53s	remaining: 17.4s
177:	learn: -0.1341359	total: 9.59s	remaining: 17.3s
178:	learn: -0.1333684	total: 9.64s	remaining: 17.3s
179:	learn: -0.1326099	total: 9.69s	remaining: 17.2s


319:	learn: -0.0810078	total: 17.3s	remaining: 9.75s
320:	learn: -0.0808590	total: 17.4s	remaining: 9.7s
321:	learn: -0.0807079	total: 17.4s	remaining: 9.64s
322:	learn: -0.0805677	total: 17.5s	remaining: 9.59s
323:	learn: -0.0804415	total: 17.5s	remaining: 9.53s
324:	learn: -0.0803208	total: 17.6s	remaining: 9.48s
325:	learn: -0.0801796	total: 17.7s	remaining: 9.42s
326:	learn: -0.0800403	total: 17.7s	remaining: 9.36s
327:	learn: -0.0799076	total: 17.7s	remaining: 9.31s
328:	learn: -0.0797709	total: 17.8s	remaining: 9.25s
329:	learn: -0.0796467	total: 17.8s	remaining: 9.19s
330:	learn: -0.0795226	total: 17.9s	remaining: 9.14s
331:	learn: -0.0793879	total: 18s	remaining: 9.09s
332:	learn: -0.0792593	total: 18s	remaining: 9.03s
333:	learn: -0.0791289	total: 18.1s	remaining: 8.97s
334:	learn: -0.0789954	total: 18.1s	remaining: 8.92s
335:	learn: -0.0788697	total: 18.2s	remaining: 8.86s
336:	learn: -0.0787500	total: 18.2s	remaining: 8.81s
337:	learn: -0.0786200	total: 18.3s	remaining: 8.75

478:	learn: -0.0700211	total: 27.1s	remaining: 1.19s
479:	learn: -0.0699893	total: 27.2s	remaining: 1.13s
480:	learn: -0.0699564	total: 27.2s	remaining: 1.07s
481:	learn: -0.0699257	total: 27.3s	remaining: 1.02s
482:	learn: -0.0698910	total: 27.3s	remaining: 961ms
483:	learn: -0.0698779	total: 27.4s	remaining: 905ms
484:	learn: -0.0698510	total: 27.4s	remaining: 848ms
485:	learn: -0.0698404	total: 27.5s	remaining: 792ms
486:	learn: -0.0698041	total: 27.5s	remaining: 735ms
487:	learn: -0.0697906	total: 27.6s	remaining: 678ms
488:	learn: -0.0697611	total: 27.6s	remaining: 622ms
489:	learn: -0.0697453	total: 27.7s	remaining: 565ms
490:	learn: -0.0697109	total: 27.7s	remaining: 508ms
491:	learn: -0.0696782	total: 27.8s	remaining: 452ms
492:	learn: -0.0696579	total: 27.8s	remaining: 395ms
493:	learn: -0.0696333	total: 27.9s	remaining: 339ms
494:	learn: -0.0696008	total: 27.9s	remaining: 282ms
495:	learn: -0.0695883	total: 28s	remaining: 226ms
496:	learn: -0.0695564	total: 28s	remaining: 169

137:	learn: -0.1728447	total: 7.06s	remaining: 18.5s
138:	learn: -0.1715777	total: 7.11s	remaining: 18.5s
139:	learn: -0.1703373	total: 7.16s	remaining: 18.4s
140:	learn: -0.1690952	total: 7.21s	remaining: 18.3s
141:	learn: -0.1678751	total: 7.25s	remaining: 18.3s
142:	learn: -0.1666732	total: 7.31s	remaining: 18.3s
143:	learn: -0.1654803	total: 7.36s	remaining: 18.2s
144:	learn: -0.1643067	total: 7.42s	remaining: 18.2s
145:	learn: -0.1631504	total: 7.48s	remaining: 18.1s
146:	learn: -0.1620116	total: 7.52s	remaining: 18.1s
147:	learn: -0.1608800	total: 7.59s	remaining: 18s
148:	learn: -0.1597719	total: 7.63s	remaining: 18s
149:	learn: -0.1586754	total: 7.68s	remaining: 17.9s
150:	learn: -0.1575910	total: 7.73s	remaining: 17.9s
151:	learn: -0.1565222	total: 7.78s	remaining: 17.8s
152:	learn: -0.1554670	total: 7.83s	remaining: 17.8s
153:	learn: -0.1544197	total: 7.88s	remaining: 17.7s
154:	learn: -0.1533870	total: 7.92s	remaining: 17.6s
155:	learn: -0.1523662	total: 7.99s	remaining: 17.

...

382:	learn: -0.0480323	total: 28.1s	remaining: 8.58s
383:	learn: -0.0479820	total: 28.2s	remaining: 8.51s
384:	learn: -0.0479418	total: 28.2s	remaining: 8.44s
385:	learn: -0.0479173	total: 28.3s	remaining: 8.36s
386:	learn: -0.0478868	total: 28.4s	remaining: 8.29s
387:	learn: -0.0478635	total: 28.5s	remaining: 8.22s
388:	learn: -0.0478316	total: 28.5s	remaining: 8.14s
389:	learn: -0.0477820	total: 28.6s	remaining: 8.07s
390:	learn: -0.0477345	total: 28.7s	remaining: 8s
391:	learn: -0.0476992	total: 28.8s	remaining: 7.93s
392:	learn: -0.0476896	total: 28.8s	remaining: 7.85s
393:	learn: -0.0476465	total: 28.9s	remaining: 7.78s
394:	learn: -0.0476096	total: 29s	remaining: 7.71s
395:	learn: -0.0475950	total: 29.1s	remaining: 7.63s
396:	learn: -0.0475864	total: 29.1s	remaining: 7.56s
397:	learn: -0.0475508	total: 29.2s	remaining: 7.49s
398:	learn: -0.0475306	total: 29.3s	remaining: 7.41s
399:	learn: -0.0475042	total: 29.4s	remaining: 7.34s
400:	learn: -0.0474648	total: 29.4s	remaining: 7.26

40:	learn: -0.4197701	total: 2.46s	remaining: 27.6s
41:	learn: -0.4151568	total: 2.53s	remaining: 27.6s
42:	learn: -0.4106128	total: 2.59s	remaining: 27.6s
43:	learn: -0.4061388	total: 2.65s	remaining: 27.5s
44:	learn: -0.4017313	total: 2.71s	remaining: 27.4s
45:	learn: -0.3973876	total: 2.77s	remaining: 27.3s
46:	learn: -0.3931092	total: 2.83s	remaining: 27.2s
47:	learn: -0.3888946	total: 2.89s	remaining: 27.2s
48:	learn: -0.3847409	total: 2.95s	remaining: 27.2s
49:	learn: -0.3806493	total: 3.02s	remaining: 27.2s
50:	learn: -0.3766175	total: 3.09s	remaining: 27.2s
51:	learn: -0.3726468	total: 3.15s	remaining: 27.2s
52:	learn: -0.3687343	total: 3.21s	remaining: 27.1s
53:	learn: -0.3648779	total: 3.28s	remaining: 27.1s
54:	learn: -0.3610751	total: 3.33s	remaining: 27s
55:	learn: -0.3573284	total: 3.4s	remaining: 26.9s
56:	learn: -0.3536341	total: 3.46s	remaining: 26.9s
57:	learn: -0.3499942	total: 3.52s	remaining: 26.9s
58:	learn: -0.3464050	total: 3.59s	remaining: 26.8s
59:	learn: -0.3

198:	learn: -0.1185287	total: 12.1s	remaining: 18.3s
199:	learn: -0.1179394	total: 12.1s	remaining: 18.2s
200:	learn: -0.1173536	total: 12.2s	remaining: 18.1s
201:	learn: -0.1167795	total: 12.3s	remaining: 18.1s
202:	learn: -0.1161972	total: 12.3s	remaining: 18s
203:	learn: -0.1156134	total: 12.4s	remaining: 18s
204:	learn: -0.1150610	total: 12.4s	remaining: 17.9s
205:	learn: -0.1145136	total: 12.5s	remaining: 17.8s
206:	learn: -0.1139708	total: 12.6s	remaining: 17.8s
207:	learn: -0.1134287	total: 12.6s	remaining: 17.7s
208:	learn: -0.1128966	total: 12.7s	remaining: 17.7s
209:	learn: -0.1123522	total: 12.7s	remaining: 17.6s
210:	learn: -0.1118064	total: 12.8s	remaining: 17.5s
211:	learn: -0.1112767	total: 12.9s	remaining: 17.5s
212:	learn: -0.1107596	total: 12.9s	remaining: 17.4s
213:	learn: -0.1102370	total: 13s	remaining: 17.4s
214:	learn: -0.1097271	total: 13s	remaining: 17.3s
215:	learn: -0.1092323	total: 13.1s	remaining: 17.2s
216:	learn: -0.1087268	total: 13.2s	remaining: 17.2s
2

357:	learn: -0.0751513	total: 21.6s	remaining: 8.55s
358:	learn: -0.0750734	total: 21.6s	remaining: 8.49s
359:	learn: -0.0749698	total: 21.7s	remaining: 8.43s
360:	learn: -0.0748788	total: 21.7s	remaining: 8.37s
361:	learn: -0.0747804	total: 21.8s	remaining: 8.31s
362:	learn: -0.0746809	total: 21.9s	remaining: 8.25s
363:	learn: -0.0745825	total: 21.9s	remaining: 8.19s
364:	learn: -0.0744878	total: 22s	remaining: 8.13s
365:	learn: -0.0744082	total: 22s	remaining: 8.07s
366:	learn: -0.0743283	total: 22.1s	remaining: 8s
367:	learn: -0.0742390	total: 22.1s	remaining: 7.94s
368:	learn: -0.0741538	total: 22.2s	remaining: 7.88s
369:	learn: -0.0740710	total: 22.3s	remaining: 7.82s
370:	learn: -0.0739830	total: 22.3s	remaining: 7.76s
371:	learn: -0.0739010	total: 22.4s	remaining: 7.7s
372:	learn: -0.0738147	total: 22.4s	remaining: 7.64s
373:	learn: -0.0737274	total: 22.5s	remaining: 7.58s
374:	learn: -0.0736457	total: 22.6s	remaining: 7.52s
375:	learn: -0.0735687	total: 22.6s	remaining: 7.46s
3

(-0.014540718608748946,
 {'depth': 4, 'learning_rate': 0.01, 'random_seed': 400})

In [89]:
from catboost import CatBoostClassifier

model = CatBoostClassifier(learning_rate=0.01, depth=4, random_seed=400)
model.fit(X_train, y_train, cat_features = cat_features)

0:	learn: 0.6718518	total: 49.2ms	remaining: 49.1s
1:	learn: 0.6514332	total: 99.8ms	remaining: 49.8s
2:	learn: 0.6322533	total: 135ms	remaining: 44.8s
3:	learn: 0.6132918	total: 170ms	remaining: 42.2s
4:	learn: 0.5953136	total: 206ms	remaining: 40.9s
5:	learn: 0.5781601	total: 228ms	remaining: 37.7s
6:	learn: 0.5614559	total: 267ms	remaining: 37.9s
7:	learn: 0.5452616	total: 325ms	remaining: 40.3s
8:	learn: 0.5296178	total: 363ms	remaining: 40s
9:	learn: 0.5143927	total: 397ms	remaining: 39.3s
10:	learn: 0.4990793	total: 430ms	remaining: 38.7s
11:	learn: 0.4813443	total: 460ms	remaining: 37.8s
12:	learn: 0.4677243	total: 513ms	remaining: 38.9s
13:	learn: 0.4516935	total: 562ms	remaining: 39.6s
14:	learn: 0.4389213	total: 607ms	remaining: 39.9s
15:	learn: 0.4267730	total: 640ms	remaining: 39.3s
16:	learn: 0.4148492	total: 668ms	remaining: 38.6s
17:	learn: 0.4034954	total: 701ms	remaining: 38.2s
18:	learn: 0.3925506	total: 758ms	remaining: 39.2s
19:	learn: 0.3818863	total: 813ms	remaini

165:	learn: 0.0738332	total: 8.86s	remaining: 44.5s
166:	learn: 0.0737117	total: 8.95s	remaining: 44.6s
167:	learn: 0.0736144	total: 9.05s	remaining: 44.8s
168:	learn: 0.0734524	total: 9.14s	remaining: 45s
169:	learn: 0.0732945	total: 9.2s	remaining: 44.9s
170:	learn: 0.0731841	total: 9.24s	remaining: 44.8s
171:	learn: 0.0730064	total: 9.27s	remaining: 44.6s
172:	learn: 0.0729036	total: 9.3s	remaining: 44.5s
173:	learn: 0.0728183	total: 9.34s	remaining: 44.3s
174:	learn: 0.0726676	total: 9.38s	remaining: 44.2s
175:	learn: 0.0725181	total: 9.41s	remaining: 44.1s
176:	learn: 0.0723727	total: 9.45s	remaining: 43.9s
177:	learn: 0.0722421	total: 9.48s	remaining: 43.8s
178:	learn: 0.0720756	total: 9.53s	remaining: 43.7s
179:	learn: 0.0719811	total: 9.57s	remaining: 43.6s
180:	learn: 0.0718267	total: 9.62s	remaining: 43.5s
181:	learn: 0.0717293	total: 9.65s	remaining: 43.4s
182:	learn: 0.0716124	total: 9.69s	remaining: 43.2s
183:	learn: 0.0715004	total: 9.74s	remaining: 43.2s
184:	learn: 0.07

326:	learn: 0.0662976	total: 14.9s	remaining: 30.8s
327:	learn: 0.0662835	total: 15s	remaining: 30.7s
328:	learn: 0.0662698	total: 15s	remaining: 30.6s
329:	learn: 0.0662650	total: 15s	remaining: 30.5s
330:	learn: 0.0662557	total: 15.1s	remaining: 30.5s
331:	learn: 0.0662496	total: 15.1s	remaining: 30.4s
332:	learn: 0.0662255	total: 15.1s	remaining: 30.3s
333:	learn: 0.0662170	total: 15.2s	remaining: 30.3s
334:	learn: 0.0661829	total: 15.2s	remaining: 30.2s
335:	learn: 0.0661797	total: 15.3s	remaining: 30.2s
336:	learn: 0.0661693	total: 15.3s	remaining: 30.1s
337:	learn: 0.0661598	total: 15.4s	remaining: 30.1s
338:	learn: 0.0661564	total: 15.4s	remaining: 30s
339:	learn: 0.0661394	total: 15.4s	remaining: 30s
340:	learn: 0.0661200	total: 15.5s	remaining: 29.9s
341:	learn: 0.0661001	total: 15.5s	remaining: 29.8s
342:	learn: 0.0660932	total: 15.5s	remaining: 29.7s
343:	learn: 0.0660865	total: 15.6s	remaining: 29.7s
344:	learn: 0.0660746	total: 15.6s	remaining: 29.6s
345:	learn: 0.0660714	

490:	learn: 0.0648685	total: 21.8s	remaining: 22.6s
491:	learn: 0.0648644	total: 21.9s	remaining: 22.6s
492:	learn: 0.0648584	total: 21.9s	remaining: 22.5s
493:	learn: 0.0648546	total: 21.9s	remaining: 22.5s
494:	learn: 0.0648513	total: 22s	remaining: 22.4s
495:	learn: 0.0648481	total: 22s	remaining: 22.3s
496:	learn: 0.0648453	total: 22s	remaining: 22.3s
497:	learn: 0.0648402	total: 22.1s	remaining: 22.3s
498:	learn: 0.0648330	total: 22.1s	remaining: 22.2s
499:	learn: 0.0648275	total: 22.2s	remaining: 22.2s
500:	learn: 0.0648248	total: 22.3s	remaining: 22.2s
501:	learn: 0.0648230	total: 22.3s	remaining: 22.1s
502:	learn: 0.0648150	total: 22.4s	remaining: 22.1s
503:	learn: 0.0648106	total: 22.4s	remaining: 22s
504:	learn: 0.0648100	total: 22.4s	remaining: 22s
505:	learn: 0.0647976	total: 22.5s	remaining: 21.9s
506:	learn: 0.0647950	total: 22.5s	remaining: 21.9s
507:	learn: 0.0647693	total: 22.6s	remaining: 21.9s
508:	learn: 0.0647683	total: 22.7s	remaining: 21.9s
509:	learn: 0.0647357	

651:	learn: 0.0641371	total: 32.3s	remaining: 17.2s
652:	learn: 0.0641315	total: 32.3s	remaining: 17.2s
653:	learn: 0.0641264	total: 32.4s	remaining: 17.1s
654:	learn: 0.0641246	total: 32.4s	remaining: 17.1s
655:	learn: 0.0641178	total: 32.5s	remaining: 17s
656:	learn: 0.0641162	total: 32.6s	remaining: 17s
657:	learn: 0.0641118	total: 32.6s	remaining: 17s
658:	learn: 0.0641101	total: 32.7s	remaining: 16.9s
659:	learn: 0.0641060	total: 32.7s	remaining: 16.9s
660:	learn: 0.0641034	total: 32.8s	remaining: 16.8s
661:	learn: 0.0641027	total: 32.8s	remaining: 16.8s
662:	learn: 0.0641012	total: 32.9s	remaining: 16.7s
663:	learn: 0.0640992	total: 32.9s	remaining: 16.6s
664:	learn: 0.0640956	total: 32.9s	remaining: 16.6s
665:	learn: 0.0640937	total: 33s	remaining: 16.5s
666:	learn: 0.0640933	total: 33s	remaining: 16.5s
667:	learn: 0.0640899	total: 33.1s	remaining: 16.4s
668:	learn: 0.0640862	total: 33.1s	remaining: 16.4s
669:	learn: 0.0640833	total: 33.2s	remaining: 16.4s
670:	learn: 0.0640778	

810:	learn: 0.0635311	total: 40.4s	remaining: 9.41s
811:	learn: 0.0635286	total: 40.4s	remaining: 9.36s
812:	learn: 0.0635267	total: 40.4s	remaining: 9.3s
813:	learn: 0.0635259	total: 40.5s	remaining: 9.25s
814:	learn: 0.0635132	total: 40.5s	remaining: 9.2s
815:	learn: 0.0635093	total: 40.6s	remaining: 9.14s
816:	learn: 0.0635072	total: 40.6s	remaining: 9.1s
817:	learn: 0.0635029	total: 40.7s	remaining: 9.05s
818:	learn: 0.0634978	total: 40.8s	remaining: 9.01s
819:	learn: 0.0634948	total: 40.8s	remaining: 8.96s
820:	learn: 0.0634919	total: 40.8s	remaining: 8.9s
821:	learn: 0.0634873	total: 40.9s	remaining: 8.85s
822:	learn: 0.0634856	total: 40.9s	remaining: 8.8s
823:	learn: 0.0634803	total: 41s	remaining: 8.76s
824:	learn: 0.0634762	total: 41s	remaining: 8.7s
825:	learn: 0.0634755	total: 41.1s	remaining: 8.65s
826:	learn: 0.0634742	total: 41.1s	remaining: 8.61s
827:	learn: 0.0634721	total: 41.2s	remaining: 8.55s
828:	learn: 0.0634687	total: 41.2s	remaining: 8.5s
829:	learn: 0.0634677	t

972:	learn: 0.0630301	total: 48.2s	remaining: 1.34s
973:	learn: 0.0630293	total: 48.2s	remaining: 1.29s
974:	learn: 0.0630271	total: 48.3s	remaining: 1.24s
975:	learn: 0.0630239	total: 48.3s	remaining: 1.19s
976:	learn: 0.0630235	total: 48.4s	remaining: 1.14s
977:	learn: 0.0630213	total: 48.4s	remaining: 1.09s
978:	learn: 0.0630183	total: 48.4s	remaining: 1.04s
979:	learn: 0.0630179	total: 48.5s	remaining: 990ms
980:	learn: 0.0630157	total: 48.6s	remaining: 941ms
981:	learn: 0.0630135	total: 48.6s	remaining: 892ms
982:	learn: 0.0630095	total: 48.7s	remaining: 842ms
983:	learn: 0.0630063	total: 48.8s	remaining: 793ms
984:	learn: 0.0630052	total: 48.8s	remaining: 744ms
985:	learn: 0.0630046	total: 48.9s	remaining: 694ms
986:	learn: 0.0630016	total: 49s	remaining: 645ms
987:	learn: 0.0629988	total: 49s	remaining: 596ms
988:	learn: 0.0629954	total: 49.1s	remaining: 546ms
989:	learn: 0.0629916	total: 49.1s	remaining: 496ms
990:	learn: 0.0629895	total: 49.2s	remaining: 447ms
991:	learn: 0.06

In [90]:
cb_pred = model.predict(X_test)
print('Final prediction:', mean_squared_error(cb_pred, y_test))

Final prediction: 0.01489312801654792


#### Ответ:
1) Stacking на LogisticRegression(), RandomForestClassifier()  
0.014671397976517413

2) XGBoost на GridSearchCV 0.01489312801654792

3) CatBoost на GridSearchCV 0.01489312801654792